In [1]:
import pandas as pd
import altair as alt
import unidecode
import geobr
from datetime import date, timedelta

In [2]:
%load_ext pycodestyle_magic
%flake8_on

In [3]:
recent = (date.today() - timedelta(days=1)).strftime("%Y-%m-%d")

In [4]:
def decodar(coluna):
    decode = [unidecode.unidecode(m).upper() for m in coluna]
    return decode

In [5]:
brasil = pd.read_excel(f"./Saude_csvs/{recent}.xlsx")
brasil = brasil[brasil['data'] == recent]
brasil.head()

regiao estado    municipio  coduf    codmun  codRegiaoSaude  \
78         Brasil    NaN          NaN     76       NaN             NaN   
123  Centro-Oeste     MS  Alcinópolis     50  500025.0         50001.0   
128  Centro-Oeste     MS      Amambai     50  500060.0         50003.0   
153  Centro-Oeste     MS   Bataguassu     50  500190.0         50004.0   
201  Centro-Oeste     MS    Batayporã     50  500200.0         50003.0   

    nomeRegiaoSaude        data  semanaEpi  populacaoTCU2019  casosAcumulado  \
78              NaN  2020-05-14         20       210147125.0          202918   
123    Campo Grande  2020-05-14         20            5343.0               1   
128        Dourados  2020-05-14         20           39396.0               2   
153     Três Lagoas  2020-05-14         20           23024.0               3   
201        Dourados  2020-05-14         20           11329.0               6   

     obitosAcumulado  Recuperadosnovos  emAcompanhamentoNovos  
78             13993           79479.0               109446.0  
123                0               NaN                    NaN  
128                0               NaN                    NaN  
153                0               NaN                    NaN  
201                2               NaN                    NaN

In [6]:
estados = list(brasil['estado'].unique())
del estados[0]

In [7]:
municipios = brasil[~brasil['municipio'].isnull()]
municipios.head()

regiao estado    municipio  coduf    codmun  codRegiaoSaude  \
123  Centro-Oeste     MS  Alcinópolis     50  500025.0         50001.0   
128  Centro-Oeste     MS      Amambai     50  500060.0         50003.0   
153  Centro-Oeste     MS   Bataguassu     50  500190.0         50004.0   
201  Centro-Oeste     MS    Batayporã     50  500200.0         50003.0   
208  Centro-Oeste     MS   Bela Vista     50  500210.0         50001.0   

    nomeRegiaoSaude        data  semanaEpi  populacaoTCU2019  casosAcumulado  \
123    Campo Grande  2020-05-14         20            5343.0               1   
128        Dourados  2020-05-14         20           39396.0               2   
153     Três Lagoas  2020-05-14         20           23024.0               3   
201        Dourados  2020-05-14         20           11329.0               6   
208    Campo Grande  2020-05-14         20           24629.0               2   

     obitosAcumulado  Recuperadosnovos  emAcompanhamentoNovos  
123                0               NaN                    NaN  
128                0               NaN                    NaN  
153                0               NaN                    NaN  
201                2               NaN                    NaN  
208                0               NaN                    NaN

## Example: Rio Grande do Sul

In [8]:
RS = municipios.query("estado=='RS'")
RS.loc[:, 'municipio'] = decodar(RS.loc[:, 'municipio'])

/home/jvfe/miniconda3/envs/wikidata/lib/python3.8/site-packages/pandas/core/indexing.py:966: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s


In [10]:
mapa = geobr.read_municipality(code_muni='RS', year=2018)
mapa.rename(columns={'name_muni': 'municipio'}, inplace=True)
mapa.loc[:, 'municipio'] = decodar(mapa.loc[:, 'municipio'])

In [11]:
full = pd.merge(mapa, RS, on='municipio',  how='left')

In [12]:
full["casosAcumulado"] = full["casosAcumulado"].fillna(0)

natural_order = ["0",
                 "1-10",
                 "11-50",
                 "51-500",
                 ">500",
                 ">1000",
                 ">10000"]

full["casos_categorizados"] = pd.cut(full["casosAcumulado"],
                                     bins=[-1, 1, 10,
                                     50, 500, 1000,
                                     10000, 100000000],
                                     labels=natural_order)

Instructions on how to add save function to altair:
* https://github.com/altair-viz/altair_saver#nodejs - Had to npm install vega too
* https://github.com/altair-viz/altair_saver/issues/13

In [14]:
alt.Chart(full).mark_geoshape(
    stroke="lightgray",
    strokeOpacity=0.2
).encode(
    alt.Color('casos_categorizados:O',
              sort=natural_order,
              scale=alt.Scale(scheme='lightorange'))
).properties(
    width=450,
    height=300
).configure_legend(
    title=None
).configure_view(
    strokeWidth=0
)  #.save(f"RS_{recent}.svg", method='node')

alt.Chart(...)

15:4: E262 inline comment should start with '# '


## Now running for all states
This takes some time (though not as much as I had imagined)

I'm saving maps as svg, but pngs are also an option, [some discussion about that here](https://en.wikipedia.org/wiki/Wikipedia:Blank_maps)

In [ ]:
for est in estados:
    estado = municipios.query("estado==@est")
    estado.loc[:, 'municipio'] = decodar(estado.loc[:, 'municipio'])
    mapa = geobr.read_municipality(code_muni=f"{est}", year=2018)
    mapa.rename(columns={'name_muni': 'municipio'}, inplace=True)
    mapa.loc[:, 'municipio'] = decodar(mapa.loc[:, 'municipio'])
    full = pd.merge(mapa, estado, on='municipio',  how='left')
    full["casosAcumulado"] = full["casosAcumulado"].fillna(0)

    natural_order = ["0",
                     "1-10",
                     "11-50",
                     "51-500",
                     ">500",
                     ">1000",
                     ">10000"]

    full["casos_categorizados"] = pd.cut(full["casosAcumulado"],
                                         bins=[-1, 1, 10,
                                         50, 500, 1000,
                                         10000, 100000000],
                                         labels=natural_order)
    alt.Chart(full).mark_geoshape(
        stroke="lightgray",
        strokeOpacity=0.2
    ).encode(
        alt.Color('casos_categorizados:O',
                  sort=natural_order,
                  scale=alt.Scale(scheme='lightorange'))
    ).properties(
        width=450,
        height=300
    ).configure_legend(
        title=None
    ).configure_view(
        strokeWidth=0
    ).save(f"./fig/{est}_{recent}.svg", method='node')